In [1]:
import requests
import pandas as pd
from datetime import datetime
from tqdm import tqdm

BINANCE_CANDLE_COLUMNS = ['opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime',
                          'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

def binance_recursive_fetch_2(coins, interval, starttime, endtime, data_type='spot'):
    all_coins_result = {}
    data_list = []
    call_dict = {}
    
    for coin in tqdm(coins):
        result_list = []
        current_time = starttime
        call = 0
        timestamps = []
        
        while current_time < endtime:
            if ((int((endtime - current_time) / (1000 * 60))) + 1) >= 1000:
                limit = 1000
            else:
                limit = int((endtime - current_time) / (1000 * 60) + 1)
            
            if data_type == 'spot':
                url = (f'https://api.binance.com/api/v3/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            elif data_type == 'futures':
                url = (f'https://fapi.binance.com/fapi/v1/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            
            result_list += requests.get(url).json()
            
            if result_list:
                # Update current_time with the timestamp of the last data point fetched, plus 1 minute (60000 ms)
                current_time = result_list[-1][0] + 60000
                timestamps.append(current_time)
                call += 1
                
                # Check if the last fetched timestamp is greater than or equal to endtime
                if current_time >= endtime:
                    print(f"Reached endtime at {datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')}. Stopping fetch.")
                    break
                
                print((datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')) + 
                      f' status : {current_time < endtime}, time : {current_time}, limit : {call * 2}')
            
            # Ensure there's no continuous fetching of the same timestamp
            if len(timestamps) > 1 and timestamps[-1] == timestamps[-2]:
                print("Duplicate timestamp detected. Stopping fetch.")
                break
            
            # Sleep if needed to avoid rate limiting (adjust based on your rate limit)
            # time.sleep(0.1)  # Uncomment if needed
            
        current_df = pd.DataFrame(result_list, columns=BINANCE_CANDLE_COLUMNS)
        current_df['coin'] = coin
        current_df = current_df[['coin'] + BINANCE_CANDLE_COLUMNS]
        current_df = current_df.values.tolist()
        
        data_list += current_df
        call_dict.update({coin: call})
    
    return {'data': data_list, 'call': call_dict}

# Set endtime to the current time (today)
endtime = int(datetime.utcnow().timestamp() * 1000)

# # Example usage with today's date as the end time
# sample_spot = binance_recursive_fetch_2(
#     ['USDT'],
#     '1m',
#     starttime=int(pd.to_datetime('2023-01-01 00:00', utc=True).timestamp() * 1000),
#     endtime=endtime,
#     data_type='spot'  # Fetch spot data
# )

# print(sample_spot['data'])

In [2]:
# Fetch NEAR USDT
sample_spot = binance_recursive_fetch_2(
    ['NEAR'],
    '1h',
    starttime=int(pd.to_datetime('2020-01-01 00:00', utc=True).timestamp() * 1000),
    endtime=endtime,
    data_type='futures'  # Fetch spot data
)

print(sample_spot['data'])

  0%|          | 0/1 [00:00<?, ?it/s]

2020-11-25 23:01:00 status : True, time : 1606345260000, limit : 2
2021-01-06 15:01:00 status : True, time : 1609945260000, limit : 4
2021-02-17 07:01:00 status : True, time : 1613545260000, limit : 6
2021-03-30 23:01:00 status : True, time : 1617145260000, limit : 8
2021-05-11 15:01:00 status : True, time : 1620745260000, limit : 10
2021-06-22 07:01:00 status : True, time : 1624345260000, limit : 12
2021-08-02 23:01:00 status : True, time : 1627945260000, limit : 14
2021-09-13 15:01:00 status : True, time : 1631545260000, limit : 16
2021-10-25 07:01:00 status : True, time : 1635145260000, limit : 18
2021-12-05 23:01:00 status : True, time : 1638745260000, limit : 20
2022-01-16 15:01:00 status : True, time : 1642345260000, limit : 22
2022-02-27 07:01:00 status : True, time : 1645945260000, limit : 24
2022-04-09 23:01:00 status : True, time : 1649545260000, limit : 26
2022-05-21 15:01:00 status : True, time : 1653145260000, limit : 28
2022-07-02 07:01:00 status : True, time : 1656745260

100%|██████████| 1/1 [00:06<00:00,  6.47s/it]

2024-12-12 12:01:00 status : True, time : 1734004860000, limit : 76
Duplicate timestamp detected. Stopping fetch.
[['NEAR', 1602748800000, '1.0625', '1.1872', '1.0625', '1.1169', '1449407', 1602752399999, '1655530.2133', 9968, '766784', '877991.5024', '0'], ['NEAR', 1602752400000, '1.1169', '1.1301', '1.0778', '1.1179', '1616432', 1602755999999, '1789316.4020', 8743, '873713', '968436.2178', '0'], ['NEAR', 1602756000000, '1.1176', '1.1650', '1.1136', '1.1570', '1270406', 1602759599999, '1441662.5443', 8310, '721173', '819075.0290', '0'], ['NEAR', 1602759600000, '1.1572', '1.1575', '1.1210', '1.1279', '481575', 1602763199999, '550378.6871', 4446, '227307', '260084.0777', '0'], ['NEAR', 1602763200000, '1.1286', '1.1812', '1.1025', '1.1536', '1835160', 1602766799999, '2107977.0163', 9266, '934671', '1074641.8592', '0'], ['NEAR', 1602766800000, '1.1532', '1.2231', '1.1521', '1.2192', '2608201', 1602770399999, '3103868.7409', 14186, '1473742', '1755919.1054', '0'], ['NEAR', 1602770400000, '

In [3]:
# Define the column names for the DataFrame based on the Binance API response structure
columns = ['coin', 'opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime', 
           'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

# Convert the list of data into a DataFrame
df = pd.DataFrame(sample_spot['data'], columns=columns)

# Show the first few rows of the DataFrame
df

coin       opentime openprice highprice lowprice closeprice   volume  \
0      NEAR  1602748800000    1.0625    1.1872   1.0625     1.1169  1449407   
1      NEAR  1602752400000    1.1169    1.1301   1.0778     1.1179  1616432   
2      NEAR  1602756000000    1.1176    1.1650   1.1136     1.1570  1270406   
3      NEAR  1602759600000    1.1572    1.1575   1.1210     1.1279   481575   
4      NEAR  1602763200000    1.1286    1.1812   1.1025     1.1536  1835160   
...     ...            ...       ...       ...      ...        ...      ...   
36456  NEAR  1733990400000    7.0790    7.1800   7.0780     7.1800  1252786   
36457  NEAR  1733994000000    7.1790    7.2200   7.1460     7.1490  1535789   
36458  NEAR  1733997600000    7.1490    7.1560   7.0210     7.0380  2065246   
36459  NEAR  1734001200000    7.0380    7.0510   6.9450     7.0070  1712135   
36460  NEAR  1734004800000    7.0070    7.1100   7.0070     7.0740   666197   

           closetime    quotevolume  trades taker_buy_volume taker_buy_quote  \
0      1602752399999   1655530.2133    9968           766784     877991.5024   
1      1602755999999   1789316.4020    8743           873713     968436.2178   
2      1602759599999   1441662.5443    8310           721173     819075.0290   
3      1602763199999    550378.6871    4446           227307     260084.0777   
4      1602766799999   2107977.0163    9266           934671    1074641.8592   
...              ...            ...     ...              ...             ...   
36456  1733993999999   8950481.6760   20675           658195    4702461.6320   
36457  1733997599999  11035337.6330   23363           709728    5101661.0870   
36458  1734001199999  14617311.6290   35347           875286    6193253.0990   
36459  1734004799999  11972018.0770   32840           797708    5579540.4890   
36460  1734008399999   4701966.5050   11536           369402    2607601.0680   

      unused  
0          0  
1          0  
2          0  
3          0  
4          0  
...      ...  
36456      0  
36457      0  
36458      0  
36459      0  
36460      0  

[36461 rows x 13 columns]

In [4]:
df.to_csv('NEAR_USDT_futures_data_2020.csv', index=False)

print("DataFrame has been saved to csv")

DataFrame has been saved to csv
